In [1]:
import matplotlib.pyplot as plt
from collections import namedtuple
import pprint
#from ase.build import molecule
#from weas_widget import WeasWidget
#from matplotlib.ticker import ScalarFormatter
import glob
#from collections import defaultdict
from pathlib import Path
import numpy as np
import csv
import pandas as pd
pd.set_option('display.width', 1000)
pd.set_option('display.float_format', '{:e}'.format)
import math
#from lmfit.models import QuadraticModel, LorentzianModel

### List the named calculation directory you created with Full_Polarization.py. This is the point of entry for all data analysis.

In [2]:
parent_dir = "/home/sethshj/Programs/Cr_data/13NOV24" 

### List the references that were downloaded from Full_polarization.py.
(Future task includes doing a check between this notebook and Full_polarization.py to ensure that the references are the same, rather
than hard coding it like this)

In [3]:
reference_cifs_mp_id = {
       "mp-644481", #Sc
       "mp-1215", #Ti
       "mp-18937", #V
       "mp-19177", #Cr
       "mp-510408", #Mn
       "mp-19770", #Fe
       "mp-22408", #Co
       "mp-19009", #Ni
       "mp-704645", #Cu
       "mp-2133" #Zn
    }

### List the elements that yo uwant to study 

In [4]:
transition_metals = {
    "Sc", "Ti", "V", "Cr", "Mn", "Fe", "Co", "Ni", "Cu", "Zn"
}

### Initialize useful functions

In [5]:
def read_corvus_cfavg_xes_out_file_to_df(corvus_cfavg_xes_out_file_path:Path):
    print(f"Processing {corvus_cfavg_xes_out_file_path.parent.name}")
    
    corvus_cfavg_xes_out_df = pd.read_csv(
        corvus_cfavg_xes_out_file_path,
        index_col='Energy',
        sep=r'\s+',
        header=None,
        names=['Energy',
               f'x_polarization',
               f'y_polarization',
               f'z_polarization',
               f'Isotropic']
        )

    corvus_cfavg_xes_out_df.attrs["Name"] = corvus_cfavg_xes_out_file_path.parent.name 
    #corvus_cfavg_xes_out_df['Energy'] = corvus_cfavg_xes_out_df['Energy'].round(2)
    
    #print(corvus_cfavg_xes_out_df)
    #print(corvus_cfavg_xes_out_df.shape)
    
    return corvus_cfavg_xes_out_df

In [6]:
def calculate_difference_and_create_new_df(corvus_cfavg_xes_out_df_1, corvus_cfavg_xes_out_df_2):
    """
    Calculate the difference between two corvus.cfavg.xes.out dataframes and create a new dataframe
    that includes the differences, with the .attrs["Name"] attribute reflecting the difference.

    ARGS:
    corvus_cfavg_xes_out_df_1 / corvus_cfavg_xes_out_df_2: DataFrames containing polarization and isotropic data
    
    RETURNS:
    difference_df: A new dataframe that includes the differences between the two input dataframes
    """
    # Initialize a dataframe to store the differences
    difference_df = pd.DataFrame()

    # List of columns to calculate the difference for
    columns_to_compare = ['x_polarization', 'y_polarization', 'z_polarization', 'Isotropic']

    # Calculate the difference for each column and add it to the difference dataframe
    for col in columns_to_compare:
        difference_df[col] = corvus_cfavg_xes_out_df_1[col] - corvus_cfavg_xes_out_df_2[col]

    # Set the .attrs["Name"] for the difference dataframe
    difference_df.attrs["Name"] = f"Difference between {corvus_cfavg_xes_out_df_1.attrs['Name']} and {corvus_cfavg_xes_out_df_2.attrs['Name']}"

    return difference_df

In [7]:
def plot_corvus_cfavg_xes_out_df(corvus_cfavg_xes_out_df):
    """
    Plot the differences in the DataFrame using matplotlib.

    Args:
        difference_df (pd.DataFrame): The DataFrame with the subtracted values.
    """
    plt.figure(figsize=(10, 6))
    
    # Plot each of the columns in the difference DataFrame
    plt.plot(corvus_cfavg_xes_out_df.index, corvus_cfavg_xes_out_df.iloc[:, 0], label='x_polarization', color='b')
    plt.plot(corvus_cfavg_xes_out_df.index, corvus_cfavg_xes_out_df.iloc[:, 1], label='y_polarization', color='g')
    plt.plot(corvus_cfavg_xes_out_df.index, corvus_cfavg_xes_out_df.iloc[:, 2], label='z_polarization', color='r')
    plt.plot(corvus_cfavg_xes_out_df.index, corvus_cfavg_xes_out_df.iloc[:, 3], label='Isotropic', color='black')
    
    # Add labels and title
    plt.xlabel('Energy')
    plt.ylabel('Intensity (arb. units)')
    plt.title(f'Polarization and Isotropic of {corvus_cfavg_xes_out_df.attrs["Name"]}')
    
    # Display a legend
    plt.legend()
    
    # Display grid for better readability
    plt.grid(True)
    
    # Show the plot
    plt.show()

In [17]:
def create_metal_dictionaries(parent_dir, transition_metals, reference_cifs_mp_id):
    list_of_metal_dictionaries = []

    for metal in transition_metals:
        metal_dictionary = {}
        metal_dictionary["Metal"] = metal
        print(f"This is the metal dictionary that was just created {metal_dictionary}")

        for reference_mp_id in reference_cifs_mp_id:
            xes_reference_pattern = f"{parent_dir}/{reference_mp_id}/{reference_mp_id}_{metal}/Corvus.cfavg.xes.out"
            xes_reference_path = Path(xes_reference_pattern)

            if xes_reference_path.exists():
                reference_df = read_corvus_cfavg_xes_out_file_to_df(xes_reference_path)
                metal_dictionary["Reference DF"] = reference_df
                print(f"This is the reference {xes_reference_path.parent.name} data frame that was just added to the metal dictionary {metal_dictionary}")
            
                xes_file_pattern = f"{parent_dir}/**/**_{metal}/Corvus.cfavg.xes.out"
                xes_file_list = glob.glob(xes_file_pattern, recursive=True)
                print(f"This is the rest of the data files for this metal we are gonna work on {xes_file_list}")

                if "Data DFs" not in metal_dictionary:
                    metal_dictionary["Data DFs"] = []

                for xes_file in xes_file_list:
                    xes_file_path = Path(xes_file)

                    if xes_file_path != xes_reference_path:
                        data_df = read_corvus_cfavg_xes_out_file_to_df(xes_file_path)
                        metal_dictionary["Data DFs"].append(data_df)
                    
                list_of_metal_dictionaries.append(metal_dictionary)

            else:
                pass
    
    print("This is the list of all the metal dictionaries")
    #pprint.pprint(list_of_metal_dictionaries)

    return list_of_metal_dictionaries

In [18]:
list_of_metal_dictionaries = create_metal_dictionaries(parent_dir, transition_metals, reference_cifs_mp_id)

This is the metal dictionary that was just created {'Metal': 'Cu'}
Processing mp-704645_Cu
This is the reference mp-704645_Cu data frame that was just added to the metal dictionary {'Metal': 'Cu', 'Reference DF':               x_polarization  y_polarization  z_polarization    Isotropic
Energy                                                                   
8.957364e+03    7.847570e-06    7.196470e-06    7.701756e-06 7.581932e-06
8.957464e+03    7.571303e-06    6.915652e-06    7.424380e-06 7.303778e-06
8.957564e+03    7.296871e-06    6.636665e-06    7.148838e-06 7.027458e-06
8.957664e+03    7.030219e-06    6.365346e-06    6.881043e-06 6.758870e-06
8.957764e+03    6.768229e-06    6.098546e-06    6.617874e-06 6.494883e-06
...                      ...             ...             ...          ...
8.991964e+03    3.717563e-06    2.000472e-06    3.238650e-06 2.985562e-06
8.992064e+03    3.631364e-06    1.962365e-06    3.167339e-06 2.920356e-06
8.992164e+03    3.548659e-06    1.925828e-06   

In [19]:
pprint.pprint(list_of_metal_dictionaries)

[{'Data DFs': [              x_polarization  y_polarization  z_polarization    Isotropic
Energy                                                                   
8.959636e+03    6.105708e-06    6.220705e-06    6.220704e-06 6.182372e-06
8.959736e+03    5.864204e-06    5.980188e-06    5.980188e-06 5.941527e-06
8.959836e+03    5.638312e-06    5.755296e-06    5.755295e-06 5.716301e-06
8.959936e+03    5.421264e-06    5.539272e-06    5.539272e-06 5.499936e-06
8.960036e+03    5.200411e-06    5.319477e-06    5.319477e-06 5.279788e-06
...                      ...             ...             ...          ...
8.994236e+03    1.704330e-06    1.810691e-06    1.810691e-06 1.775237e-06
8.994336e+03    1.672883e-06    1.777189e-06    1.777188e-06 1.742420e-06
8.994436e+03    1.642587e-06    1.744879e-06    1.744878e-06 1.710781e-06
8.994536e+03    1.613379e-06    1.713698e-06    1.713698e-06 1.680259e-06
8.994636e+03    1.585203e-06    1.683590e-06    1.683590e-06 1.650794e-06

[351 rows x 4 columns]

In [21]:
def compare_and_realign_corvus_cfavg_xes_out_dfs(corvus_cfavg_xes_out_df_1, corvus_cfavg_xes_out_df_2):
    """
    The Energy columns of the corvus xes out files are not exactly lined up.
    We do this to the dataframes so we align them. We specifically use merge_asof 
    because I don't want to do extra interpolation, and these Energy columns are so close
    together in values that it matches them up for us.

    ARGS:
    corvus_cfavg_xes_out_df_1 / corvus_cfavg_xes_out_df_2 = corvus cfavg xes out dfs
    
    RETURNS:
    aligned _df: A new dataframe that is aligned by the Energy column that is the index.
    """

    aligned_df = pd.merge_asof(corvus_cfavg_xes_out_df_1,
                                corvus_cfavg_xes_out_df_2,
                                left_index=True,
                                right_index=True,
                                suffixes= [str(corvus_cfavg_xes_out_df_1.attrs['Name']), str(corvus_cfavg_xes_out_df_2.attrs['Name'])],
                                direction='nearest')
    
    aligned_df.attrs["Name"] = f"Calculation: {corvus_cfavg_xes_out_df_1.attrs["Name"]} and Reference:{corvus_cfavg_xes_out_df_2.attrs["Name"]}"
    
    return aligned_df

In [22]:
def reference_and_xes_df_alignment(list_of_metal_dictionaries):
    aligned_df_list = []

    for metal_dict in list_of_metal_dictionaries:
        reference_df = metal_dict.get("Reference DF")
        data_dfs = metal_dict.get("Data DFs", [])

        for data_df in data_dfs:
            aligned_df = compare_and_realign_corvus_cfavg_xes_out_dfs(data_df, reference_df)
            aligned_df_list.append(aligned_df)
    return aligned_df_list

In [23]:
aligned_df_list = reference_and_xes_df_alignment(list_of_metal_dictionaries)
print(aligned_df_list)

[              x_polarizationmp-1032331_Cu  y_polarizationmp-1032331_Cu  z_polarizationmp-1032331_Cu  Isotropicmp-1032331_Cu  x_polarizationmp-704645_Cu  y_polarizationmp-704645_Cu  z_polarizationmp-704645_Cu  Isotropicmp-704645_Cu
Energy                                                                                                                                                                                                                                
8.959636e+03                 6.105708e-06                 6.220705e-06                 6.220704e-06            6.182372e-06                3.688597e-06                2.868858e-06                3.500323e-06           3.352593e-06
8.959736e+03                 5.864204e-06                 5.980188e-06                 5.980188e-06            5.941527e-06                3.608590e-06                2.776875e-06                3.417221e-06           3.267562e-06
8.959836e+03                 5.638312e-06                 5.755296e-06     

In [24]:
def create_subtracted_df(aligned_df):
    """
    Create a new DataFrame with the reference columns subtracted from the data columns.

    Args:
        aligned_df (pd.DataFrame): The aligned DataFrame containing reference and data columns.

    Returns:
        pd.DataFrame: A DataFrame with the reference subtracted from the data columns.
    """
    difference_df = pd.DataFrame()

    difference_df['x_polarization_diff'] = np.sqrt(np.abs(aligned_df.iloc[:,0]**2 - aligned_df.iloc[:,4]**2))
    difference_df['y_polarization_diff'] =  np.sqrt(np.abs(aligned_df.iloc[:,1]**2 - aligned_df.iloc[:,5]**2))
    difference_df['z_polarization_diff'] = np.sqrt(np.abs(aligned_df.iloc[:,2]**2 - aligned_df.iloc[:,6]**2))
    difference_df['Isotropic_diff'] = np.sqrt(np.abs(aligned_df.iloc[:,3]**2 - aligned_df.iloc[:,7]**2))

    difference_df.attrs["Name"] = f"{aligned_df.attrs["Name"]}"
    
    return difference_df


In [25]:
linear_background_subtraction_list = []

for aligned_df in aligned_df_list:
    subtracted_df = create_subtracted_df(aligned_df)
    linear_background_subtraction_list.append(subtracted_df)
    print(subtracted_df)
    print(aligned_df.attrs["Name"])
    #plot_corvus_cfavg_xes_out_df(aligned_df)

print(len(aligned_df_list))


              x_polarization_diff  y_polarization_diff  z_polarization_diff  Isotropic_diff
Energy                                                                                     
8.959636e+03         4.865585e-06         5.519676e-06         5.142460e-06    5.194405e-06
8.959736e+03         4.622441e-06         5.296377e-06         4.907673e-06    4.962336e-06
8.959836e+03         4.392252e-06         5.087334e-06         4.686450e-06    4.744026e-06
8.959936e+03         4.167102e-06         4.885497e-06         4.471237e-06    4.532044e-06
8.960036e+03         3.930681e-06         4.676921e-06         4.246676e-06    4.311383e-06
...                           ...                  ...                  ...             ...
8.994236e+03         2.933838e-06         4.125705e-07         2.353662e-06    2.086969e-06
8.994336e+03         2.951882e-06         5.389040e-07         2.379060e-06    2.114446e-06
8.994436e+03         2.968848e-06         6.357794e-07         2.402858e-06    2

## Initial Examinations

### 1. Visually inspect the data

### Reference spectra to delete linear background

### Calculated Spectra

### Linear background subtraction

### 2. Choose the best anisotropy and isotropy candidates for the job
##### (Open project: determine an algorithm to quantify anisotropy and give the user best possible candidates)

In [26]:
###EXPECTED ANISOTROPY###

#input only the name of the material from the .cif file.
#ex: if you calculated FeO.cif, just input 'FeO' in the list.
anistropic_materials_name = ['', '']

anisotropic_matching_files = []
for aniso_material in anistropic_materials_name:
    for metal in transition_metals:
        
        # Use glob to search for files of the anisotropy material name, and the transition metal appears after the underscore
        pattern = f'{parent_dir}**/{aniso_material}_{metal}/Corvus.cfavg.xes.out'
        anistropic_materials_name.extend(glob.glob(pattern, recursive=True))
    
print(f'These are the matching_files list: {anisotropic_matching_files}')

###EXPECTED ISOTROPY###
isotropic_materials_name = ['', '']

isotropic_matching_files = []
for iso_material in isotropic_materials_name:
    for metal in transition_metals:
        
        # Use glob to search for files where the transition metal appears after the underscore
        pattern = f'{parent_dir}**/{iso_material}_{metal}/Corvus.cfavg.xes.out'
        isotropic_materials_name.extend(glob.glob(pattern, recursive=True))

print(f'These are the matching_files list: {isotropic_matching_files}')

These are the matching_files list: []
These are the matching_files list: []


### 3. Do some math and check if it makes sense

In [27]:
def xes_integrated_abs_difference(data_1, data_2):
    ''' 
    Calculate the integrated absolute difference of Δμ(E) for data_1 and data_2.

    Data 1 and 2 have orthogonal polarizations.

    Parameters:
    data_1 (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization 1.
    data_2 (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization 2.

    Returns:
    difference (float): The integrated absolute difference of Δμ(E) between the two datasets.
    '''
    # Calculate the absolute difference of Delta mu(E)
    abs_difference = np.abs(data_1 - data_2)

    # Integrate the absolute difference over the energy range
    integrated_abs_difference = np.sum(abs_difference)

    return integrated_abs_difference

aniso_integrated_diff = xes_integrated_abs_difference()


TypeError: xes_integrated_abs_difference() missing 2 required positional arguments: 'data_1' and 'data_2'

In [28]:
def xes_average(data_1, data_2, data_3):
    '''
    Calculates the integral of the average of 3 orthogonally polarized XES spectra.

    Parameters:
    data_1 (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization 1.
    data_2 (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization 2.
    data_3 (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization 3.

    Return:
    integrated_average (float): The integral of the average of the 3 spectra.
    '''
    # Calculate the average of Delta mu(E) values
    average_delta_muE = (data_1 + data_2 + data_3) / 3

    # Integrate the average Delta mu(E) over the energy range
    integrated_average = np.sum(average_delta_muE)

    return integrated_average



In [29]:
def anisotropy_parameter(xes_difference, xes_average):
    '''
    Calculate the anisotropy parameter, which is the quotient of the XES difference and the XES average.

    Parameters:
    xes_difference (float): The integrated absolute difference of Δμ(E).
    xes_average (float): The integral of the average of the 3 spectra.

    Returns:
    float: The anisotropy parameter.
    '''
    if xes_average == 0:
        raise ValueError(
            "The xes_average must not be zero to avoid division by zero.")

    return xes_difference / xes_average


In [30]:

def anisotropy_matrix(data_x, data_y, data_z):
    '''
    Calculate a 3x3 anisotropy matrix where each entry represents the anisotropy parameter 
    for the difference between two datasets divided by the average of all three datasets.

    Parameters:
    data_x (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization x.
    data_y (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization y.
    data_z (pandas.DataFrame): The DataFrame containing the X-ray absorption data for polarization z.

    Returns:
    numpy.ndarray: A 3x3 anisotropy matrix.
    '''
    # Calculate the XES average of all three datasets
    xes_avg = xes_average(data_x, data_y, data_z)

    # Initialize a 3x3 matrix
    anisotropy_mat = np.zeros((3, 3))

    # Define the pairs for which to calculate the differences
    pairs = [(data_x, data_y), (data_x, data_z), (data_y, data_z)]

    # Fill the anisotropy matrix with the anisotropy parameters
    for i, (data1, data2) in enumerate(pairs):
        diff = xes_integrated_abs_difference(data1, data2)
        anisotropy_mat[i][(i+1) % 3] = anisotropy_parameter(diff, xes_avg)
        anisotropy_mat[(i+1) % 3][i] = anisotropy_mat[i][(i+1) %
                                                         3]  # Symmetric entries

    return anisotropy_mat

In [31]:
#def read_data(file):
#    return np.loadtxt(file)

output_txt = f'{parent_dir}anisotropy_data.csv'

# Open the CSV file for writing
with open(output_txt, mode='w', newline='') as file_out:
    txt_writer = csv.writer(file_out, delimiter= '\t')
    
    # Write the header row
    txt_writer.writerow(['parent_dir', 'm00', 'm01', 'm02', 'm10', 'm11', 'm12', 'm20', 'm21', 'm22'])
    
    # Loop through each matching file and process the data
    for file in linear_background_subtraction_list:
        data = file
        data_x = data.iloc[:, 0]
        data_y = data.iloc[:, 1]
        data_z = data.iloc[:, 2]
        
        # Calculate the anisotropy matrix (3x3)
        anisotropy_mat = anisotropy_matrix(data_x, data_y, data_z)
        
        # Get the parent directory name
        #parent_dir = os.path.basename(os.path.dirname(file))
        
        # Flatten the 3x3 matrix into a single row (list)
        flattened_matrix = anisotropy_mat.flatten().tolist()
        
        # Prepend the parent_dir to the flattened matrix row
        row = [parent_dir] + flattened_matrix
        
        # Write the row to the CSV
        txt_writer.writerow(row)

print(f"Data has been written to {output_txt}")
    

Data has been written to /home/sethshj/Programs/Cr_data/13NOV24anisotropy_data.csv


# (WIP) PROBABILITY DISTRIBUTION PARAMETER GUESSER
##### Perhaps some deconvolution data science can be in order?

In [ ]:
def LORENTZIAN_MODEL(center, num, sigma= 0.15, amp= 4000):
    """We know we want to set up lots of Lorentzians. Here is a function that sets one up fast.
    The function will stay in all caps unlike regular functions because I'm too lazy to change it after the
    first time I wrote this. This will be filled with data at the bottom of the cell"""

    model = LorentzianModel(prefix= num)
    modelparams = model.make_params()
    modelparams[num + 'center'].set(center)
    modelparams[num + 'amplitude'].set(amp)
    modelparams[num + 'sigma'].set(sigma, min=0)
    return model, modelparams

def central_limit_theorem_slope_change(independent_column, dependent_column)->list:
    """This takes two columns of data (Corvus.cfavg.out, XMU.dat, or any other spectral data in two columns)
    and conducts the central limit theorem. We store the zero points and put them in a list for our model guesser."""
    
    zipped_data = list(zip(independent_column, dependent_column))
    
    slope_changes = []
    
    for i in range(1, len(zipped_data) - 1):
        x1, y1 = zipped_data[i-1]  
        x2, y2 = zipped_data[i]    
        x3, y3 = zipped_data[i+1]
        
        slope1 = (y2 - y1) / (x2 - x1) if (x2 - x1) != 0 else 0
        slope2 = (y3 - y2) / (x3 - x2) if (x3 - x2) != 0 else 0
        

        if slope1 > 0 and slope2 < 0:
            slope_changes.append(x2)  # store the point where the change occurs. We only want the x (eV). If you want both poits, insert (x2,y2) instead
    
    return slope_changes

#BigModel= QuadraticModel(label= 'Background')
#AllParams= BigModel.make_params(a=0, b=0, c=0)

for file in matching_files:
    data = read_data(file)
    energy = data[:, 0]
    data_x = data[:, 1]
    data_y = data[:, 2]
    data_z = data[:, 3]
    data_isotropic = data[:, 4]

slope_changes_x_pol = central_limit_theorem_slope_change(data[:, 0],data[:, 1])
#slope_changes_y_pol = central_limit_theorem_slope_change(data[: 0],data[: 2])
#slope_changes_z_pol = central_limit_theorem_slope_change(data[: 0],data[: 3])
#slope_changes_isotropic = central_limit_theorem_slope_change(data[: 0],data[: 4])

print(slope_changes_x_pol)
AllParams = None
BigModel = []

for i, cen in enumerate(slope_changes_x_pol):
    model, modelparams = LORENTZIAN_MODEL(cen, 'data%d_' % (i+1) )
    AllParams = None
    BigModel = model
    AllParams.update(modelparams)

calculation = BigModel.eval(AllParams, x= data_x)
calculation_fit = BigModel.fit(data[:, 0], AllParams, x= data_x)
calculationVariables = calculation_fit.eval_components()

print(calculation_fit.fit_report(min_correl=0.5))

plt.plot(energy, data_x, label = 'X Polarization')
plt.plot(energy, calculation_fit.best_fit, label='best fit')
for name, comp in calculationVariables.items():
    plt.plot(data[:, 0], comp, '--', label=name)
plt.legend()
plt.title('Lines of best fit')
plt.xlabel('Energy (eV)')
plt.ylabel('Relative Intensity (arb. units)')
plt.show()
myfig = plt.figure(figsize=(12,9)) 